# Extensions

The purpose of this notebook is to test everything related to merging initial hits

In [1]:
import os
import sys

module_path = os.path.abspath(os.path.join('../..'))
if module_path not in sys.path:
    sys.path.append(module_path)

from testing_framework import testing_utils
import database
from preprocessing import preprocessing_utils, merge_search, clustering
from identification import create_hits
from gen_spectra import get_precursor, gen_spectrum
import utils

import operator

max_peptide_length = 23
ppm_tolerance = 20
precursor_tolerance = 10
peak_filter = 25
relative_abundance_filter = 0.1

import matplotlib.pyplot as plt

In [2]:
datasets = testing_utils.define_data()

dataset = datasets[0]

input_spectra_path = [os.path.join(dataset[0], 'NOD2_E3.mzML')]
input_spectra, boundaries = preprocessing_utils.load_spectra(input_spectra_path, ppm_tolerance, peak_filter=peak_filter, relative_abundance_filter=relative_abundance_filter)

correct_sequences = testing_utils.generate_truth_set(datasets[0])

path = dataset[2]
db = database.build(path)

In [ ]:
write_path = os.path.abspath(os.path.join(module_path, 'intermediate_files'))
matched_masses_b, matched_masses_y, kmer_set = merge_search.modified_match_masses(boundaries, db, max_peptide_length, True, write_path)
print('Finished matching masses')

On protein 28/279 [10%]

In [ ]:
print(len(matched_masses_b), len(matched_masses_y))

In [ ]:
unique_b,unique_y = testing_utils.get_unique_matched_masses(boundaries, matched_masses_b, matched_masses_y)

# Getting initial hits

In [ ]:
for i, seq in enumerate(correct_sequences):
    if len(seq) > 30:
        print(i)

In [ ]:
spectrum_num = 5

correct_sequence = correct_sequences[spectrum_num]
print(correct_sequence)

input_spectrum = input_spectra[spectrum_num]

In [ ]:
location = os.path.join(os.path.abspath(os.path.join('../..')), 'intermediate_files/')
b_hits, y_hits = create_hits(spectrum_num, input_spectrum, matched_masses_b, matched_masses_y, False, location)
correct_hits = testing_utils.append_correct_hits(correct_sequence, input_spectrum, ppm_tolerance)
ion = 'b'
clusters = testing_utils.create_clusters(ion, b_hits, y_hits)
b_sorted_clusters = testing_utils.Bayes_clusters(ion, clusters, location, kmer_set, unique_b)
ion = 'y'
clusters = testing_utils.create_clusters(ion, b_hits, y_hits)
y_sorted_clusters = testing_utils.Bayes_clusters(ion, clusters, location, kmer_set, unique_y)
with open(os.path.join(location, 'b_sorted_clusters.txt'), 'w') as b:
    [b.write(str(x) + '\n') for x in b_sorted_clusters]
with open(os.path.join(location, 'y_sorted_clusters.txt'), 'w') as y:
    [y.write(str(x) + '\n') for x in y_sorted_clusters]
print(len(b_hits), len(y_hits), len(boundaries), len(input_spectra))
print(len(clusters), len(b_sorted_clusters), len(y_sorted_clusters))

# Printing hits

In [ ]:
b_sorted_clusters = sorted(b_sorted_clusters, key=operator.attrgetter('score', 'pid'), reverse = True)
testing_utils.write_b_sorted_cluster(b_sorted_clusters)
for i in range(0, 50):
    x = b_sorted_clusters[i]
    score = x.score
    seq = x.seq
    print(score, seq)

In [ ]:
y_sorted_clusters = sorted(y_sorted_clusters, key=operator.attrgetter('prob', 'score', 'pid'))
# y_sorted_clusters = sorted(y_sorted_clusters, key=operator.attrgetter('score', 'prob', 'pid'), reverse = True)
testing_utils.write_y_sorted_cluster(y_sorted_clusters)
for i in range(0, 50):
    x = y_sorted_clusters[i]
    score = x.score
    seq = x.seq
    print(score, seq)
for i, cluster in enumerate(y_sorted_clusters):
    x = y_sorted_clusters[i]

# Merging

In [ ]:
m = clustering.Ryan_merge(b_sorted_clusters, y_sorted_clusters)
m.sort(key = lambda x: x[0], reverse = True)
[print(m[x]) for x in range(0,10)]
print(len(m))

In [ ]:
def filter_by_precursor(mseqs, obs_prec, precursor_tol, charge):
    filtered_seqs = []
    for comb_seq in mseqs:
        b_seq = comb_seq[3][4]
        y_seq = comb_seq[4][4]
        if b_seq != y_seq:
            new_seq = b_seq + y_seq
        else:
            new_seq = b_seq
        tol = utils.ppm_to_da(obs_prec, precursor_tol)
        if not (get_precursor(new_seq, charge) > obs_prec + tol):
            filtered_seqs.append(comb_seq)
    return filtered_seqs

m = filter_by_precursor(m, input_spectrum.precursor_mass, precursor_tolerance, input_spectrum.precursor_charge)
[print(m[x]) for x in range(0,10)]

In [ ]:
print(len(m))
print(m[:50])

# Hybrid Merge

In [20]:
from constants import WATER_MASS, PROTON_MASS
import collections

def min_info(cluster):
    return (cluster.pid, cluster.start, cluster.end, cluster.score, cluster.seq)

def check_for_hybrid_overlap(b_seq, y_seq, ion):
    match = True
    print('code got here')
    if ion == 'b':
        for i, char in enumerate(b_seq):
            if char == y_seq[0]:
                k = 0
                for j in range(i, len(b_seq) + 1):
                    if b_seq[j] != y_seq[k]:
                        match = False
                        break
        if match == True:
            print('Match was true for', b_seq)
            modified_seq = b_seq[:i]
    else:
        for i, char in enumerate(y_seq):
            if char == y_seq[0]:
                k = 0
                for j in range(i, len(b_seq) + 1):
                    if b_seq[j] != y_seq[k]:
                        match = False
                        break
        if match == True:
            print('Match was true for', b_seq)
            modified_seq = b_seq[:i]
    return match, modified_seq

def grab_matches(b,indexed_clusters, target_val, ion):
    #Given a cluster we want to find everything that it can pair with
    # It can pair with anything up to a certain mass 
    current_index = 0
    matches = []
    for key in indexed_clusters.keys():
        if key<=target_val: #if key is a valid key
            for y in indexed_clusters[key]:
                if ion == 'b':
                    matches.append((b.score + y.score, b.end - y.start, y.end-b.start,min_info(b), min_info(y)))
                else:
                    matches.append((b.score + y.score, b.end - y.start, y.end-b.start,min_info(y), min_info(b)))
        else:
#             match, modified_seq = check_for_hybrid_overlap()
            break            
    return matches
    
def index_by_precursor_mass(sorted_clusters, pc):
    indexed = dict()
    for y in sorted_clusters:
        if get_precursor(y.seq, pc) not in indexed.keys():
            indexed[get_precursor(y.seq, pc)] = []
        indexed[get_precursor(y.seq, pc)].append(y)
    indexed = collections.OrderedDict(sorted(indexed.items(),key=lambda t: t[0]))
    return indexed
    
def get_hybrid_matches(b_sorted_clusters, y_sorted_clusters, obs_prec, precursor_tol, charge):
    merged_seqs = []
    ind_b, ind_y = index_by_precursor_mass(b_sorted_clusters, charge),index_by_precursor_mass(y_sorted_clusters, charge)
    for i, cluster in enumerate(b_sorted_clusters[:10]):
        cluster_seq = cluster.seq
        cluster_mass = get_precursor(cluster_seq, charge)
        tol = utils.ppm_to_da(obs_prec, precursor_tol)
        if not (cluster_mass > obs_prec + tol):
            diff = obs_prec + tol - cluster_mass + (charge * PROTON_MASS) + WATER_MASS
            merges = grab_matches(cluster,ind_y, diff, 'b')
            [merged_seqs.append(x) for x in merges]
    for i, cluster in enumerate(y_sorted_clusters[:10]):
        cluster_seq = cluster.seq
        cluster_mass = get_precursor(cluster_seq, charge)
        tol = utils.ppm_to_da(obs_prec, precursor_tol)
        if not (cluster_mass > obs_prec + tol):
            diff = obs_prec + tol - cluster_mass + (charge * PROTON_MASS) + WATER_MASS
#             print(get_precursor(cluster_seq + 'DL', charge), obs_prec + tol)
            merges = grab_matches(cluster,ind_b, diff, 'y')
            [merged_seqs.append(x) for x in merges]

    merged_seqs.sort(key=lambda a: a[0], reverse=True)
    return merged_seqs

#All inputs are the same
merged_seqs = clustering.get_hybrid_matches(b_sorted_clusters, y_sorted_clusters, input_spectrum.precursor_mass, precursor_tolerance, input_spectrum.precursor_charge)
print(len(merged_seqs))
[print(x) for x in merged_seqs[:50]]
with open(os.path.join(location, 'merged_seqs.txt'), 'w') as b:
    [b.write(str(x) + '\n') for x in merged_seqs]

120744
(17, 14, 15, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (126, 60, 75, 6, 'DPQVAQLELGGGPGAG'))
(17, 15, 14, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (126, 60, 75, 6, 'DPQVAQLELGGGPGAG'))
(15, -63, 85, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (134, 137, 145, 4, 'NIVEAMERF'))
(15, -3613, 3637, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (137, 3687, 3697, 4, 'HCREIICSVAF'))
(15, -735, 760, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (159, 809, 820, 4, 'EREGILQEESIY'))
(15, 6, 23, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (73, 68, 83, 4, 'ASAAGHLDDLPGALSA'))
(15, 3637, -3613, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (137, 3687, 3697, 4, 'HCREIICSVAF'))
(15, 85, -63, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (134, 137, 145, 4, 'NIVEAMERF'))
(15, 23, 6, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (73, 68, 83, 4, 'ASAAGHLDDLPGALSA'))
(15, 760, -735, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (159, 809, 820, 4, 'EREGILQEESIY'))
(14, -61, 79, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (4, 135, 139, 3, 'LNNPQ'))
(14, -1723, 1742, (126, 60

In [54]:
def hybrid_filter_by_precursor(mseqs, obs_prec, precursor_tol, charge):
    filtered_seqs = []
    for comb_seq in mseqs:
        b_seq = comb_seq[3][4]
        y_seq = comb_seq[4][4]
        if b_seq != y_seq:
            new_seq = b_seq + y_seq
        else:
            new_seq = b_seq
        tol = utils.ppm_to_da(obs_prec, precursor_tol)
        if not (get_precursor(new_seq, charge) > obs_prec + tol):
            filtered_seqs.append(comb_seq)
    return filtered_seqs

merged_seqs = hybrid_filter_by_precursor(merged_seqs, input_spectrum.precursor_mass, precursor_tolerance, input_spectrum.precursor_charge)
print(len(merged_seqs))
[print(x) for x in merged_seqs[:50]]

114916
(17, 14, 15, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (126, 60, 75, 6, 'DPQVAQLELGGGPGAG'))
(17, 15, 14, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (126, 60, 75, 6, 'DPQVAQLELGGGPGAG'))
(15, -63, 85, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (134, 137, 145, 4, 'NIVEAMERF'))
(15, -3613, 3637, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (137, 3687, 3697, 4, 'HCREIICSVAF'))
(15, -735, 760, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (159, 809, 820, 4, 'EREGILQEESIY'))
(15, 6, 23, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (73, 68, 83, 4, 'ASAAGHLDDLPGALSA'))
(15, 3637, -3613, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (137, 3687, 3697, 4, 'HCREIICSVAF'))
(15, 85, -63, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (134, 137, 145, 4, 'NIVEAMERF'))
(15, 23, 6, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (73, 68, 83, 4, 'ASAAGHLDDLPGALSA'))
(15, 760, -735, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (159, 809, 820, 4, 'EREGILQEESIY'))
(14, -61, 79, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (4, 135, 139, 3, 'LNNPQ'))
(14, -1723, 1742, (126, 60

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None]

In [55]:
def get_overlapping_sequence(b_seq, y_seq, b_start, b_end, y_start):
    seq = ''
    if y_start > b_end:
        return b_seq + y_seq
    else:
        for i in range(b_start, y_start):
            seq = seq + b_seq[i]
        return seq
def overlap(comb_seq):
    b_seq = comb_seq[3][4]
    y_seq = comb_seq[4][4]
    b_pid = comb_seq[3][0]
    y_pid = comb_seq[4][0]
    if b_pid == y_pid:
        y_start = comb_seq[4][1]
        b_end = comb_seq[3][2]
        if (y_start - b_end > 0) & (y_start - b_end < 10):
            b_start = comb_seq[3][1]
            return get_overlapping_sequence(b_seq, y_seq, b_start, b_end, y_start)
        else:
            return b_seq + y_seq
    else:
        return b_seq + y_seq

def comb_seq_precursor(comb_seq, obs_prec, precursor_tol, charge): #Currently unused. Created for testing how close initial hits are to the precursor
    new_seq = overlap(comb_seq)
    tol = utils.ppm_to_da(obs_prec, precursor_tol)
    return obs_prec + tol - get_precursor(new_seq, charge)

def find_next_mass(comb_seq, ion):
    if ion == 'b':
        b_tup = comb_seq[3]
        target_index = b_tup[2]
        target_prot = b_tup[0]
        for i, prot_name in enumerate(db.proteins):
            if i == target_prot:
                protein = db.proteins[prot_name]
                prot_seq = protein[0][1]
                to_add = prot_seq[target_index] if target_index < len(prot_seq) else ''
                    
    else:
        y_tup = comb_seq[4]
        target_index = y_tup[1]
        target_prot = y_tup[0]
        for i, prot_name in enumerate(db.proteins):
            if i == target_prot:
                protein = db.proteins[prot_name]
                prot_seq = protein[0][1]
                to_add = prot_seq[target_index] if target_index < len(prot_seq) else ''
    
    return to_add

def in_tol(mass, tolerance, queried_mass):
    if queried_mass >= mass - tol:
        if queried_mass <= mass + tol:
            return True
    return False
def filter_by_missing_mass(mseqs, obs_prec, precursor_tol, charge):
    filtered_seqs = []
    for comb_seq in mseqs:
        new_seq = overlap(comb_seq)
        tol = utils.ppm_to_da(obs_prec, precursor_tol)
        dif = obs_prec + tol - get_precursor(new_seq, charge)
#         if in_tol(obs_prec, tol, get_precursor(new_seq, charge))
        if dif <= 1: #tol can vary but i'm not sure how much. Tol is .05 for spec 4 Other hacks are 2*tol
#             print(obs_prec, get_precursor(new_seq, charge), comb_seq)
            filtered_seqs.append(comb_seq)
        else:
            next_b = find_next_mass(comb_seq, 'b')
            b_seq = comb_seq[3][4]
            y_seq = comb_seq[4][4]
            b_dif = obs_prec + tol - get_precursor(b_seq + next_b + y_seq, charge)
            next_y = find_next_mass(comb_seq, 'y')
            y_dif = obs_prec + tol - get_precursor(b_seq + next_y + y_seq, charge)
            if b_dif >= 0 and y_dif >= 0:
                filtered_seqs.append(comb_seq)
                
#             if in_tol(obs_prec, tol, get_precursor(b_seq + next_b + y_seq, charge)): #For when the entire alignment is coded
#                 filtered_seqs.append(comb_seq)
#             else:

    return filtered_seqs

merged_seqs = filter_by_missing_mass(merged_seqs, input_spectrum.precursor_mass, precursor_tolerance, input_spectrum.precursor_charge) 
print(len(merged_seqs))
[print(x) for x in merged_seqs]

105309
(15, -63, 85, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (134, 137, 145, 4, 'NIVEAMERF'))
(15, -3613, 3637, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (137, 3687, 3697, 4, 'HCREIICSVAF'))
(15, 3637, -3613, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (137, 3687, 3697, 4, 'HCREIICSVAF'))
(15, 85, -63, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (134, 137, 145, 4, 'NIVEAMERF'))
(14, -61, 79, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (4, 135, 139, 3, 'LNNPQ'))
(14, -1723, 1742, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (191, 1797, 1802, 3, 'SRGNAP'))
(14, -951, 972, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (27, 1025, 1032, 3, 'ELTAYAVD'))
(14, -970, 991, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (110, 1044, 1051, 3, 'IEDFKELT'))
(14, -263, 285, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (131, 337, 345, 3, 'LEKAGYVQS'))
(14, -1048, 1070, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (110, 1122, 1130, 3, 'NLSWELLYA'))
(14, -25, 49, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (168, 99, 109, 3, 'REESGKPGAHV'))
(14, -44, 68, (126, 60, 74, 11,

(12, -45, 62, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (86, 119, 122, 1, 'LTMF'))
(12, -10, 27, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (90, 84, 87, 1, 'TMFL'))
(12, -11, 28, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (90, 85, 88, 1, 'MFLT'))
(12, -12, 29, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (90, 86, 89, 1, 'FLTM'))
(12, -13, 30, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (90, 87, 90, 1, 'LTMF'))
(12, -157, 174, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (101, 231, 234, 1, 'FITM'))
(12, -242, 259, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (110, 316, 319, 1, 'LFMT'))
(12, 5, 12, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (114, 69, 72, 1, 'FLTM'))
(12, -1645, 1662, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (137, 1719, 1722, 1, 'LFMT'))
(12, -1416, 1433, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (158, 1490, 1493, 1, 'MFLT'))
(12, -352, 369, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (184, 426, 429, 1, 'TLFM'))
(12, -543, 560, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (191, 617, 620, 1, 'MTFL'))
(12, -664, 681, (126, 60, 74, 11, 'DP

(12, -53, 71, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (83, 127, 131, 1, 'DWNLL'))
(12, -1783, 1801, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (191, 1857, 1861, 1, 'EWVNL'))
(12, 70, -52, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (249, 4, 8, 1, 'DNWLL'))
(12, -153, 171, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (265, 227, 231, 1, 'VWINE'))
(12, -209, 228, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (18, 283, 288, 1, 'LGWGVE'))
(12, -282, 301, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (98, 356, 361, 1, 'WDLVAG'))
(12, -93, 112, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (133, 167, 172, 1, 'ADGLVW'))
(12, -222, 241, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (142, 296, 301, 1, 'WSAVPT'))
(12, -533, 552, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (145, 607, 612, 1, 'ITSPGW'))
(12, -1503, 1522, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (158, 1577, 1582, 1, 'FDGPKP'))
(12, -141, 160, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (229, 215, 220, 1, 'WSTGLP'))
(12, -243, 261, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (26, 317, 321, 1, 'DLWQV'))
(1

(12, -901, 923, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (27, 975, 983, 1, 'SATDRDAHA'))
(12, -1032, 1054, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (127, 1106, 1114, 1, 'GGGDQREPQ'))
(12, -64, 84, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (96, 138, 144, 1, 'EEKFPYM'))
(12, 26, -5, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (138, 48, 55, 1, 'FTFVCPTE'))
(12, -49, 70, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (161, 123, 130, 1, 'FTFVCPTE'))
(12, 27, -6, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (203, 47, 54, 1, 'FTFVCPTE'))
(12, -116, 137, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (145, 190, 197, 1, 'CCSYVGRR'))
(12, -629, 649, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (85, 703, 709, 1, 'MRYSCQR'))
(12, -23, 44, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (96, 97, 104, 1, 'RCPTCHNI'))
(12, -905, 925, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (191, 979, 985, 1, 'HFMQFPH'))
(12, -906, 926, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (191, 980, 986, 1, 'FMQFPHH'))
(12, -351, 371, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (142, 425, 431, 1, 

(12, -810, 833, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (76, 884, 893, 1, 'KDSKMLVDET'))
(12, 29, -5, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (31, 45, 55, 1, 'LAKSGTEDTLM'))
(12, -706, 730, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (149, 780, 790, 1, 'DVTTCLVASKE'))
(12, -331, 356, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (27, 405, 416, 1, 'SATTMVAVTVAD'))
(12, -48, 72, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (252, 122, 132, 1, 'EATLTMSLAQT'))
(12, -1060, 1082, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (131, 1134, 1142, 1, 'MRYRDNTPL'))
(12, -211, 234, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (106, 285, 294, 1, 'YANNVQRVMA'))
(12, -222, 244, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (156, 296, 304, 1, 'TERHLMHLE'))
(12, -426, 448, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (45, 500, 508, 1, 'VFYYLMMAK'))
(12, -1005, 1027, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (76, 1079, 1087, 1, 'ELFPRGYFH'))
(12, -85, 107, (126, 60, 74, 11, 'DPQVAQLELGGGPGA'), (118, 159, 167, 1, 'NFHFILFNN'))
(12, -143, 164, (126, 60, 74, 11, 'DP

...

(4, -2234, 2253, (129, 2258, 2262, 1, 'QIDGP'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -633, 652, (127, 657, 661, 1, 'TTPPN'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -63, 83, (123, 87, 92, 1, 'APAAAE'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -218, 237, (104, 242, 246, 1, 'LPDGQ'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -56, 76, (70, 80, 85, 1, 'STAPGP'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -615, 635, (67, 639, 644, 1, 'GLGADP'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -116, 136, (61, 140, 145, 1, 'PTSAGP'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -61, 81, (54, 85, 90, 1, 'AAAPAE'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -226, 246, (27, 250, 255, 1, 'APTPGS'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -228, 248, (27, 252, 257, 1, 'TPGSAP'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -79, 99, (16, 103, 108, 1, 'DAGAPV'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -317, 336, (15, 341, 345, 1, 'DLGPQ'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -558, 578, (15, 582, 587, 1, 'ATSP

(4, -775, 795, (196, 799, 804, 1, 'EASKMI'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -693, 714, (191, 717, 723, 1, 'MASLSIG'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -108, 128, (155, 132, 137, 1, 'MSKALE'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -595, 615, (149, 619, 624, 1, 'SKLDCL'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -882, 902, (137, 906, 911, 1, 'LCVSKE'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -1144, 1165, (131, 1168, 1174, 1, 'SSLGMAL'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -34, 54, (103, 58, 63, 1, 'SAIMEK'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -142, 163, (101, 166, 172, 1, 'MGLALSS'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -357, 378, (68, 381, 387, 1, 'SSLCGVI'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -1358, 1378, (45, 1382, 1387, 1, 'DVKMVS'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -56, 76, (31, 80, 85, 1, 'MKELAS'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -57, 77, (31, 81, 86, 1, 'KELASM'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, 17, 4, (21, 7, 1

(4, -960, 982, (45, 984, 991, 1, 'IYVLDYLN'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -254, 277, (39, 278, 286, 1, 'VLLVGYGYE'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -34, 56, (256, 58, 65, 1, 'LFYVDLDK'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -279, 302, (110, 303, 311, 1, 'VVSYFIPST'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -280, 303, (110, 304, 312, 1, 'VSYFIPSTV'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -195, 218, (158, 219, 227, 1, 'DFLVGIFTT'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -272, 294, (178, 296, 303, 1, 'REHVMKNV'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -32, 56, (35, 56, 65, 1, 'MGNAKVKAHG'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -1226, 1248, (191, 1250, 1257, 1, 'VFRPPNPW'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -80, 101, (209, 104, 110, 1, 'MKTWRKY'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -1074, 1097, (85, 1098, 1106, 1, 'HVLCGAVKW'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -561, 584, (129, 585, 593, 1, 'LSSHVLNKD'), (244, 9, 24, 3, 'LCLAGLVFVS

(4, -144, 168, (38, 168, 177, 1, 'KNSPTFKSFE'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -202, 227, (264, 226, 236, 1, 'NGLDTFSGFKV'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -224, 249, (223, 248, 258, 1, 'WSEGVQVPSVP'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -442, 467, (49, 466, 476, 1, 'DGFKKFLESGG'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -633, 657, (249, 657, 666, 1, 'WTNNTLPLEP'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -61, 85, (152, 85, 94, 1, 'KSEKTAWTFS'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -109, 132, (43, 133, 141, 1, 'MFLMKWKNS'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -337, 362, (91, 361, 371, 1, 'LKMSSTFIGNS'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -224, 249, (11, 248, 258, 1, 'IIEASSISHMP'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -980, 1004, (131, 1004, 1013, 1, 'KDDCISKFKT'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -687, 714, (127, 711, 723, 1, 'PMSLASGSVPAAP'), (244, 9, 24, 3, 'LCLAGLVFVSEAGPAG'))
(4, -320, 346, (68, 344, 355, 1, 'LSNACALLPDPA'), (24

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

# Alignments

In [45]:
for i, comb_seq in enumerate(merged_seqs):
    b_seq = comb_seq[3][4]
    y_seq = comb_seq[4][4]
    if b_seq == "DPQV" and y_seq == "DPQVAQLELGGGPGAG":
        print(i)

4760


In [51]:
def modified_find_next_mass(cluster, ion):
    if ion == 'b':
        target_index = cluster[2]
    else:
        target_index = cluster[1]
    target_prot = cluster[0]
    for i, prot_name in enumerate(db.proteins):
        if i == target_prot:
            protein = db.proteins[prot_name]
            prot_seq = protein[0][1]
            to_add = prot_seq[target_index] if target_index < len(prot_seq) else ''
                        
    return to_add
    
def make_merge(b, y, b_seq, y_seq):
    new_b = (b[0], b[1], b[2], b[3], b_seq)
    new_y = (y[0], y[1], y[2], y[3], y_seq)
    return (b[3] + y[3], b[1] - y[2], y[2]-b[1], new_b, new_y)

def add_amino_acids(alignment_list, missing_mass, b_cluster, y_cluster, comb_seq, b_seq, y_seq, precursor_charge, prec_mass, tol):
    #This function recursively adds in amino acids    
    if abs(get_precursor(b_seq + y_seq, precursor_charge) - prec_mass) <= tol:
        alignment_list.append(make_merge(b_cluster, y_cluster, b_seq, y_seq))
        return
    
    if get_precursor(b_seq + y_seq, precursor_charge) > prec_mass + tol:
        return
    
    next_b = modified_find_next_mass(b_cluster, 'b')
    next_y = modified_find_next_mass(y_cluster, 'y')
    
    if get_precursor(b_seq + y_seq, precursor_charge) < prec_mass - tol and (next_b != ""):
        mod_b = b_seq + next_b
        add_amino_acids(alignment_list, missing_mass, b_cluster, y_cluster, comb_seq, mod_b, y_seq, precursor_charge, prec_mass, tol)
    if get_precursor(b_seq + y_seq, precursor_charge) < prec_mass - tol and (next_y != ""):
        mod_y = next_y + y_seq
        add_amino_acids(alignment_list, missing_mass, b_cluster, y_cluster, comb_seq, b_seq, mod_y, precursor_charge, prec_mass, tol)
        
    return

        
def find_alignments(merged_seqs, obs_prec, prec_charge, tol):
    alignments = []
#     for comb_seq in merged_seqs:
    comb_seq = merged_seqs[4760]
    b_cluster = comb_seq[3]
    y_cluster = comb_seq[4]
    b_seq = comb_seq[3][4]
    y_seq = comb_seq[4][4]
    if b_seq != y_seq:
        new_seq = b_seq + y_seq
        missing_mass = obs_prec - get_precursor(new_seq, prec_charge)
        new_seqs = add_amino_acids(alignments, missing_mass, b_cluster, y_cluster, comb_seq, b_seq, y_seq, prec_charge, obs_prec, tol)            
    else:
        new_seq = b_seq
        if (abs(get_precursor(new_seq, prec_charge) - obs_prec) <= tol):
            alignments.append(comb_seq)

    return alignments

print(merged_seqs[4760])
tol = utils.ppm_to_da(input_spectrum.precursor_mass, precursor_tolerance)
alignments = find_alignments(merged_seqs, input_spectrum.precursor_mass, input_spectrum.precursor_charge, tol)
print(alignments)

105309
(8, -427, 445, (76, 502, 505, 2, 'DPQV'), (126, 60, 75, 6, 'DPQVAQLELGGGPGAG'))
[]


# Second Round of Scoring

In [47]:
def score_by_dist(merged_seqs, obs_prec, precursor_tol, charge):
    new_list = []
    for comb_seq in merged_seqs:
        b_seq = comb_seq[3][4]
        y_seq = comb_seq[4][4]
        if b_seq != y_seq:
            new_seq = b_seq + y_seq
        else:
            new_seq = b_seq
        tol = utils.ppm_to_da(obs_prec, precursor_tol)
        dist = abs(get_precursor(new_seq, charge) - obs_prec)
        new_list.append((dist, comb_seq))
    return new_list
    
print("SpecMill Sequence Dist:", abs(input_spectrum.precursor_mass - get_precursor(correct_sequence, input_spectrum.precursor_charge)))
new_merges = score_by_dist(alignments, input_spectrum.precursor_mass, 10, input_spectrum.precursor_charge)
new_merges.sort(key=lambda a: a[0])
[print(x) for x in new_merges[:50]]

SpecMill Sequence Dist: 0.0053152997874121866


[]

In [49]:
def find_total_score(sequence, i_spectrum, ppm_tol):
    total_score = 0
    spectrum = gen_spectrum(sequence)
    masses = sorted(spectrum['spectrum'])
    o_ctr, t_ctr = 0, 0
    observed = i_spectrum[o_ctr]
    theoretical = masses[t_ctr]
    tol = utils.ppm_to_da(observed, ppm_tol)
    while (o_ctr < len(i_spectrum) and t_ctr < len(masses)):
        if theoretical < observed - tol:
            t_ctr = t_ctr + 1
            if t_ctr < len(masses):
                theoretical = masses[t_ctr]
        elif observed + tol < theoretical:
            o_ctr = o_ctr + 1
            if o_ctr < len(i_spectrum):
                observed = i_spectrum[o_ctr]
            tol = utils.ppm_to_da(observed, ppm_tol)
        elif observed - tol <= theoretical and observed + tol >= theoretical:
            total_score = total_score + 1
            o_ctr = o_ctr + 1
            t_ctr = t_ctr + 1
            if o_ctr < len(i_spectrum) and t_ctr < len(masses):
                observed = i_spectrum[o_ctr]
                theoretical = masses[t_ctr]
                tol = utils.ppm_to_da(observed, ppm_tol)
        
    return(total_score)

def find_for_all(merged_seqs, i_spectrum, ppm_tol):
    new_list = []
    for comb_seq in merged_seqs:
        b_seq = comb_seq[3][4]
        y_seq = comb_seq[4][4]
        if b_seq != y_seq:
            new_seq = b_seq + y_seq
        else:
            new_seq = b_seq
        score = find_total_score(new_seq, i_spectrum, ppm_tol)
        new_list.append((score, comb_seq))
        
    new_list.sort(key=lambda a: a[0], reverse = True)
    return new_list
    
    
print("SpecMill Sequence Total Score:", find_total_score(correct_sequence, input_spectrum.mz_values, ppm_tolerance))
tol = utils.ppm_to_da(input_spectrum.precursor_mass, 10)
print(input_spectrum.precursor_mass, get_precursor(correct_sequence, input_spectrum.precursor_charge), abs(input_spectrum.precursor_mass - get_precursor(correct_sequence, input_spectrum.precursor_charge)))
rescored_merges = find_for_all(alignments, input_spectrum.mz_values, ppm_tolerance)
[print(x) for x in rescored_merges[:50]]

SpecMill Sequence Total Score 13
977.48943 977.4841147002126 0.0053152997874121866


[]